In [1]:
import pandas as pd
import numpy as np
from scipy.stats import skew

In [2]:
def precise_diff(float_array):
    # Truncate down to 4 digits on the left, 6 digits on the right, and convert to int
    float_array = np.apply_along_axis(lambda x: (x % 10000)*1000000, axis=-1, arr=float_array)
    
    int_array = float_array.astype(np.int64)
    #print(int_array)

    # Calculate differences, then return to floating point value
    result = np.diff(int_array)
    #print(np.where(result < 0))
    #print(min(result))
    #print(max(result))
    result = np.apply_along_axis(lambda x: x/1000000, axis=-1, arr=result)
    #print(result)
    
    return(result)

In [2]:
def convert_to_2d_array(array_of_arrays):
    # Determine the number of rows
    num_rows = len(array_of_arrays)
    
    # Determine the number of columns (assuming all inner arrays have the same length)
    num_cols = len(array_of_arrays[0]) if num_rows > 0 else 0

    # Initialize a 2D NumPy array with the correct shape
    matrix = np.empty((num_rows, num_cols), dtype=float)

    # Populate the 2D NumPy array
    for i in range(num_rows):
        for j in range(num_cols):
            matrix[i, j] = float(array_of_arrays[i][j])
    
    return matrix

In [3]:
# Function to calculate statistics for each row
def calculate_statistics(row):
    # Convert inner arrays to numpy arrays for numerical operations
    #packets = np.array(row['Data'], dtype=float) #PROBLEM
    
    # Extract packet data and convert inner arrays to numpy arrays for numerical operations
    packets = convert_to_2d_array(row['Data'])

    # Extract the sizes
    sizes = packets[:, 2].astype(float)
    
    # Extract the timestamps
    timestamps = packets[:, 0].astype(float)
    
    # Calculate inter-arrival times as differences between consecutive timestamps
    inter_arrival_times = np.diff(timestamps)
    
    # Calculate inter-arrival time statistics
    iat_min = np.min(inter_arrival_times)
    iat_max = np.max(inter_arrival_times)
    iat_mean = np.mean(inter_arrival_times)
    iat_std = np.std(inter_arrival_times)
    iat_skew = skew(inter_arrival_times)

    # Calculate size statistics
    size_min = np.min(sizes)
    size_max = np.max(sizes)
    size_mean = np.mean(sizes)
    size_std = np.std(sizes)
    size_skew = skew(sizes)

    # Calculate general statistics
    total_packets = len(packets)
    total_bytes = np.sum(sizes)
    duration = timestamps[-1] - timestamps[0] if total_packets > 1 else 0
    packets_per_sec = total_packets / duration if duration > 0 else 0
    bytes_per_sec = total_bytes / duration if duration > 0 else 0
    
    # Return all calculated statistics as a dictionary
    return {
        'iat_min': iat_min, 'iat_max': iat_max, 'iat_mean': iat_mean, 'iat_std': iat_std, 'iat_skew': iat_skew,
        'size_min': size_min, 'size_max': size_max, 'size_mean': size_mean, 'size_std': size_std, 'size_skew': size_skew,
        'total_packets': total_packets, 'total_bytes': total_bytes, 'packets_per_sec': packets_per_sec, 'bytes_per_sec': bytes_per_sec
    }

In [4]:
# Function to calculate statistics for each row based on a given direction
def calculate_statistics_by_direction(row, direction=0):
    # Convert inner arrays to numpy arrays for numerical operations
    #packets = np.array(row['Data'], dtype=float) #problem
    
    # Extract packet data and convert inner arrays to numpy arrays for numerical operations
    packets = convert_to_2d_array(row['Data'])
    
    # Filter packets by direction
    filtered_packets = packets[packets[:, 3] == direction]
    print(packets[:,3])
    print(type(packets[:,3]))
    print(direction)
    print(type(direction))
    
    print(len(filtered_packets))

    # Extract the timestamps and sizes for filtered packets
    timestamps = filtered_packets[:, 0].astype(float)
    sizes = filtered_packets[:, 2].astype(float)

    # Calculate inter-arrival times as differences between consecutive timestamps
    inter_arrival_times = np.diff(timestamps)
    
    print(len(inter_arrival_times))

    # Calculate inter-arrival time statistics
    iat_min = np.min(inter_arrival_times) if len(inter_arrival_times) > 0 else np.nan
    iat_max = np.max(inter_arrival_times) if len(inter_arrival_times) > 0 else np.nan
    iat_mean = np.mean(inter_arrival_times) if len(inter_arrival_times) > 0 else np.nan
    iat_std = np.std(inter_arrival_times) if len(inter_arrival_times) > 0 else np.nan
    iat_skew = skew(inter_arrival_times) if len(inter_arrival_times) > 0 else np.nan

    # Calculate size statistics
    size_min = np.min(sizes)
    size_max = np.max(sizes)
    size_mean = np.mean(sizes)
    size_std = np.std(sizes)
    size_skew = skew(sizes)

    # Calculate general statistics
    total_packets = len(filtered_packets)
    total_bytes = np.sum(sizes)
    duration = timestamps[-1] - timestamps[0] if total_packets > 1 else 0
    packets_per_sec = total_packets / duration if duration > 0 else 0
    bytes_per_sec = total_bytes / duration if duration > 0 else 0

    # Return all calculated statistics as a dictionary
    return {
        'iat_min': iat_min, 'iat_max': iat_max, 'iat_mean': iat_mean, 'iat_std': iat_std, 'iat_skew': iat_skew,
        'size_min': size_min, 'size_max': size_max, 'size_mean': size_mean, 'size_std': size_std, 'size_skew': size_skew,
        'total_packets': total_packets, 'total_bytes': total_bytes, 'packets_per_sec': packets_per_sec, 'bytes_per_sec': bytes_per_sec
    }

In [5]:
def create_statistics_matrix_numpy(row):
    # Call the statistics functions
    stats_general = calculate_statistics(row)
    stats_dir0 = calculate_statistics_by_direction(row, 0)
    stats_dir1 = calculate_statistics_by_direction(row, 1)
    
    # Convert dictionaries to lists
    stats_general_list = list(stats_general.values())
    stats_dir0_list = list(stats_dir0.values())
    stats_dir1_list = list(stats_dir1.values())
    
    # Combine the lists into a single (3, 14) numpy array
    statistics_matrix = np.array([stats_general_list, stats_dir0_list, stats_dir1_list])
    
    return statistics_matrix

In [6]:
def create_statistics_matrix(row):
    # Call the statistics functions
    stats_general = calculate_statistics(row)
    stats_dir0 = calculate_statistics_by_direction(row, 0)
    stats_dir1 = calculate_statistics_by_direction(row, 1)
    
    #print(stats_dir0)
    
    # Convert dictionaries to lists
    stats_general_list = list(stats_general.values())
    stats_dir0_list = list(stats_dir0.values())
    stats_dir1_list = list(stats_dir1.values())
    
    #print(stats_dir0_list)
    
    '''
    # Ensure each list has the correct size (14 in this case)
    # If not, pad with zeros or truncate as needed
    target_size = 14
    
    def pad_or_truncate(lst, size):
        if len(lst) < size:
            return lst + [0] * (size - len(lst))
        return lst[:size]

    # Pad or truncate each list to the target size
    stats_general_list = pad_or_truncate(stats_general_list, target_size)
    stats_dir0_list = pad_or_truncate(stats_dir0_list, target_size)
    stats_dir1_list = pad_or_truncate(stats_dir1_list, target_size)
    '''

    # Combine the lists into a single list of lists
    statistics_list_of_lists = [stats_general_list, stats_dir0_list, stats_dir1_list]
    
    return statistics_list_of_lists

In [7]:
# Load DataFrame
df = pd.read_parquet('quic_text.parquet')

df

Label                                               Data  \
0          Youtube  [[1522982445.960145000, 0, 1412, 1], [15229824...   
1          Youtube  [[1522939930.491890000, 0, 1412, 1], [15229399...   
2          Youtube  [[1522994330.247572000, 0, 1412, 1], [15229943...   
3          Youtube  [[1522908947.040100000, 0, 1412, 1], [15229089...   
4          Youtube  [[1523000044.440979000, 0, 86, 1], [1523000044...   
...            ...                                                ...   
3927  Google Drive  [[1522841219.402012000, 0, 161, 1], [152284121...   
3928  Google Drive  [[1522835303.978634000, 0, 566, 1], [152283530...   
3929  Google Drive  [[1522782530.426202000, 0, 86, 1], [1522782530...   
3930  Google Drive  [[1522763269.225023000, 0, 75, 1], [1522763269...   
3931  Google Drive  [[1522845824.936935000, 0, 174, 1], [152284582...   

      num_of_packets  
0               7288  
1              22529  
2              17938  
3              22709  
4              26621  
...              ...  
3927           11682  
3928           10763  
3929           10133  
3930           15547  
3931           17175  

[3932 rows x 3 columns]

In [9]:
df.drop(columns=['num_of_packets'], inplace= True)
df

Label                                               Data
0          Youtube  [[1522982445.960145000, 0, 1412, 1], [15229824...
1          Youtube  [[1522939930.491890000, 0, 1412, 1], [15229399...
2          Youtube  [[1522994330.247572000, 0, 1412, 1], [15229943...
3          Youtube  [[1522908947.040100000, 0, 1412, 1], [15229089...
4          Youtube  [[1523000044.440979000, 0, 86, 1], [1523000044...
...            ...                                                ...
3927  Google Drive  [[1522841219.402012000, 0, 161, 1], [152284121...
3928  Google Drive  [[1522835303.978634000, 0, 566, 1], [152283530...
3929  Google Drive  [[1522782530.426202000, 0, 86, 1], [1522782530...
3930  Google Drive  [[1522763269.225023000, 0, 75, 1], [1522763269...
3931  Google Drive  [[1522845824.936935000, 0, 174, 1], [152284582...

[3932 rows x 2 columns]

In [8]:
# Initialize an empty list to store the data for the new DataFrame
data_for_new_df = []

# Iterate over each row of the original dataframe
for index, row in df.iterrows():
    # Extract the label
    label = row['Label']
    
    print(row)
    
    # Compute the statistics matrix for the current row
    statistics_matrix = create_statistics_matrix(row)
    
    # Append the label and matrix as a tuple to the list
    data_for_new_df.append({'Label': label, 'Matrix': statistics_matrix})

# Create a new DataFrame from the list of dictionaries
new_df = pd.DataFrame(data_for_new_df)

# Print the new dataframe to see the result
print(new_df)

Label                                                       Youtube
Data              [[1522982445.960145000, 0, 1412, 1], [15229824...
num_of_packets                                                 7288
Name: 0, dtype: object
[1. 1. 1. ... 1. 0. 0.]
<class 'numpy.ndarray'>
0
<class 'int'>
6207
6206
[1. 1. 1. ... 1. 0. 0.]
<class 'numpy.ndarray'>
1
<class 'int'>
1081
1080
{'iat_min': 9.5367431640625e-07, 'iat_max': 15.162935972213745, 'iat_mean': 0.009390093263717685, 'iat_std': 0.2937754218710131, 'iat_skew': 38.008513050272, 'size_min': 93.0, 'size_max': 1412.0, 'size_mean': 1393.231190591268, 'size_std': 125.56166016946129, 'size_skew': -7.555825110003967, 'total_packets': 6207, 'total_bytes': 8647786.0, 'packets_per_sec': 106.51237493567753, 'bytes_per_sec': 148396.3629443375}
[9.5367431640625e-07, 15.162935972213745, 0.009390093263717685, 0.2937754218710131, 38.008513050272, 93.0, 1412.0, 1393.231190591268, 125.56166016946129, -7.555825110003967, 6207, 8647786.0, 106.5123749356775

[1. 1. 0. ... 0. 1. 0.]
<class 'numpy.ndarray'>
0
<class 'int'>
15921
15920
[1. 1. 0. ... 0. 1. 0.]
<class 'numpy.ndarray'>
1
<class 'int'>
1661
1660
{'iat_min': 9.5367431640625e-07, 'iat_max': 8.217477083206177, 'iat_mean': 0.0037576379488460983, 'iat_std': 0.15342063744944962, 'iat_skew': 45.97967947871741, 'size_min': 72.0, 'size_max': 1392.0, 'size_mean': 1377.6843163117894, 'size_std': 104.03978000138312, 'size_skew': -8.502755358748553, 'total_packets': 15921, 'total_bytes': 21934112.0, 'packets_per_sec': 266.1413440263591, 'bytes_per_sec': 366658.7555872553}
[9.5367431640625e-07, 8.217477083206177, 0.0037576379488460983, 0.15342063744944962, 45.97967947871741, 72.0, 1392.0, 1377.6843163117894, 104.03978000138312, -8.502755358748553, 15921, 21934112.0, 266.1413440263591, 366658.7555872553]
Label                                                       Youtube
Data              [[1522936798.765282000, 0, 1412, 1], [15229367...
num_of_packets                                           

[1. 1. 1. ... 0. 1. 0.]
<class 'numpy.ndarray'>
0
<class 'int'>
17033
17032
[1. 1. 1. ... 0. 1. 0.]
<class 'numpy.ndarray'>
1
<class 'int'>
3190
3189
{'iat_min': 9.5367431640625e-07, 'iat_max': 6.060056924819946, 'iat_mean': 0.0035259362367914, 'iat_std': 0.11089602255383932, 'iat_skew': 43.17565324719947, 'size_min': 92.0, 'size_max': 1412.0, 'size_mean': 1398.1484764868196, 'size_std': 107.31144937721048, 'size_skew': -8.98307786691877, 'total_packets': 17033, 'total_bytes': 23814663.0, 'packets_per_sec': 283.6292677603427, 'bytes_per_sec': 396555.8286061954}
[9.5367431640625e-07, 6.060056924819946, 0.0035259362367914, 0.11089602255383932, 43.17565324719947, 92.0, 1412.0, 1398.1484764868196, 107.31144937721048, -8.98307786691877, 17033, 23814663.0, 283.6292677603427, 396555.8286061954]
Label                                                       Youtube
Data              [[1522975508.107613000, 0, 1412, 1], [15229755...
num_of_packets                                                144

[1. 0. 0. ... 0. 1. 0.]
<class 'numpy.ndarray'>
1
<class 'int'>
2036
2035
{'iat_min': 9.5367431640625e-07, 'iat_max': 14.960981845855713, 'iat_mean': 0.005075111434119199, 'iat_std': 0.18469703250993383, 'iat_skew': 56.51455945260929, 'size_min': 91.0, 'size_max': 1412.0, 'size_mean': 1392.3067295188557, 'size_std': 127.21442891238482, 'size_skew': -7.463816777155051, 'total_packets': 12304, 'total_bytes': 17130942.0, 'packets_per_sec': 197.05602408352712, 'bytes_per_sec': 274362.42842372454}
[9.5367431640625e-07, 14.960981845855713, 0.005075111434119199, 0.18469703250993383, 56.51455945260929, 91.0, 1412.0, 1392.3067295188557, 127.21442891238482, -7.463816777155051, 12304, 17130942.0, 197.05602408352712, 274362.42842372454]
Label                                                       Youtube
Data              [[1522960947.264354000, 0, 1412, 1], [15229609...
num_of_packets                                                16540
Name: 26, dtype: object
[1. 1. 0. ... 0. 1. 0.]
<class 'numpy

[1. 1. 1. ... 0. 1. 0.]
<class 'numpy.ndarray'>
0
<class 'int'>
17633
17632
[1. 1. 1. ... 0. 1. 0.]
<class 'numpy.ndarray'>
1
<class 'int'>
2621
2620
{'iat_min': 9.5367431640625e-07, 'iat_max': 5.12083101272583, 'iat_mean': 0.003457491497379033, 'iat_std': 0.10661860852891678, 'iat_skew': 39.80962725615694, 'size_min': 92.0, 'size_max': 1412.0, 'size_mean': 1409.037826802019, 'size_std': 57.95356558629581, 'size_skew': -20.827464022730666, 'total_packets': 17633, 'total_bytes': 24845564.0, 'packets_per_sec': 289.2434343863516, 'bytes_per_sec': 407554.9402044972}
[9.5367431640625e-07, 5.12083101272583, 0.003457491497379033, 0.10661860852891678, 39.80962725615694, 92.0, 1412.0, 1409.037826802019, 57.95356558629581, -20.827464022730666, 17633, 24845564.0, 289.2434343863516, 407554.9402044972]
Label                                                       Youtube
Data              [[1522970288.219006000, 0, 1412, 1], [15229702...
num_of_packets                                                2

...

[1. 0. 1. ... 0. 1. 0.]
<class 'numpy.ndarray'>
0
<class 'int'>
4681
4680
[1. 0. 1. ... 0. 1. 0.]
<class 'numpy.ndarray'>
1
<class 'int'>
8930
8929
{'iat_min': 0.0014269351959228516, 'iat_max': 6.58516001701355, 'iat_mean': 0.008239685470222408, 'iat_std': 0.1457822428614097, 'iat_skew': 40.73053689901367, 'size_min': 74.0, 'size_max': 1294.0, 'size_mean': 78.56697286904507, 'size_std': 43.818387826681274, 'size_skew': 21.772464481517243, 'total_packets': 4681, 'total_bytes': 367772.0, 'packets_per_sec': 121.3897883394179, 'bytes_per_sec': 9537.228207042172}
[0.0014269351959228516, 6.58516001701355, 0.008239685470222408, 0.1457822428614097, 40.73053689901367, 74.0, 1294.0, 78.56697286904507, 43.818387826681274, 21.772464481517243, 4681, 367772.0, 121.3897883394179, 9537.228207042172]
Label                                                  Google Drive
Data              [[1522889679.950305000, 0, 1412, 1], [15228896...
num_of_packets                                                 8676
N

[1. 1. 0. ... 0. 1. 0.]
<class 'numpy.ndarray'>
1
<class 'int'>
1253
1252
{'iat_min': 9.5367431640625e-07, 'iat_max': 0.22751212120056152, 'iat_mean': 0.00021559980775080146, 'iat_std': 0.0027212168883769218, 'iat_skew': 75.80392671317408, 'size_min': 89.0, 'size_max': 1412.0, 'size_mean': 1402.9302824004035, 'size_std': 83.83050465439845, 'size_skew': -10.630432331111804, 'total_packets': 7932, 'total_bytes': 11128043.0, 'packets_per_sec': 4638.807881780268, 'bytes_per_sec': 6507924.051587208}
[9.5367431640625e-07, 0.22751212120056152, 0.00021559980775080146, 0.0027212168883769218, 75.80392671317408, 89.0, 1412.0, 1402.9302824004035, 83.83050465439845, -10.630432331111804, 7932, 11128043.0, 4638.807881780268, 6507924.051587208]
Label                                                  Google Drive
Data              [[1522805601.943417000, 0, 1412, 1], [15228056...
num_of_packets                                                10980
Name: 3903, dtype: object
[1. 0. 1. ... 0. 0. 1.]
<class 

[1. 1. 0. ... 1. 0. 0.]
<class 'numpy.ndarray'>
0
<class 'int'>
8641
8640
[1. 1. 0. ... 1. 0. 0.]
<class 'numpy.ndarray'>
1
<class 'int'>
4494
4493
{'iat_min': 0.0016541481018066406, 'iat_max': 4.852605104446411, 'iat_mean': 0.0032619748678472307, 'iat_std': 0.061610718889791444, 'iat_skew': 69.79907702143146, 'size_min': 92.0, 'size_max': 1412.0, 'size_mean': 1407.5896308297652, 'size_std': 74.63893168298786, 'size_skew': -17.05677039108897, 'total_packets': 8641, 'total_bytes': 12162982.0, 'packets_per_sec': 306.5982361172439, 'bytes_per_sec': 431564.4979893285}
[0.0016541481018066406, 4.852605104446411, 0.0032619748678472307, 0.061610718889791444, 69.79907702143146, 92.0, 1412.0, 1407.5896308297652, 74.63893168298786, -17.05677039108897, 8641, 12162982.0, 306.5982361172439, 431564.4979893285]
Label                                                  Google Drive
Data              [[1522810837.656364000, 0, 215, 1], [152281083...
num_of_packets                                           

[1. 1. 0. ... 0. 0. 1.]
<class 'numpy.ndarray'>
1
<class 'int'>
795
794
{'iat_min': 9.5367431640625e-07, 'iat_max': 4.976813077926636, 'iat_mean': 0.0014474667268356092, 'iat_std': 0.07216832705953519, 'iat_skew': 61.78230522846947, 'size_min': 78.0, 'size_max': 1412.0, 'size_mean': 1400.4655293951782, 'size_std': 96.00140896530634, 'size_skew': -9.483356333721767, 'total_packets': 7093, 'total_bytes': 9933502.0, 'packets_per_sec': 690.9595815957557, 'bytes_per_sec': 967665.076230171}
[9.5367431640625e-07, 4.976813077926636, 0.0014474667268356092, 0.07216832705953519, 61.78230522846947, 78.0, 1412.0, 1400.4655293951782, 96.00140896530634, -9.483356333721767, 7093, 9933502.0, 690.9595815957557, 967665.076230171]
Label                                                  Google Drive
Data              [[1522897597.464571000, 0, 1412, 1], [15228975...
num_of_packets                                                 6750
Name: 3921, dtype: object
[1. 1. 0. ... 0. 0. 1.]
<class 'numpy.ndarray'>
0

[1. 0. 1. ... 1. 1. 0.]
<class 'numpy.ndarray'>
0
<class 'int'>
3659
3658
[1. 0. 1. ... 1. 1. 0.]
<class 'numpy.ndarray'>
1
<class 'int'>
6474
6473
{'iat_min': 9.5367431640625e-07, 'iat_max': 12.373944997787476, 'iat_mean': 0.008652120812334215, 'iat_std': 0.21690413800006375, 'iat_skew': 52.68661535303303, 'size_min': 74.0, 'size_max': 1294.0, 'size_mean': 81.30773435364854, 'size_std': 58.25998288415597, 'size_skew': 16.880748584297685, 'total_packets': 3659, 'total_bytes': 297505.0, 'packets_per_sec': 115.6101949018259, 'bytes_per_sec': 9400.003015651193}
[9.5367431640625e-07, 12.373944997787476, 0.008652120812334215, 0.21690413800006375, 52.68661535303303, 74.0, 1294.0, 81.30773435364854, 58.25998288415597, 16.880748584297685, 3659, 297505.0, 115.6101949018259, 9400.003015651193]
Label                                                  Google Drive
Data              [[1522763269.225023000, 0, 75, 1], [1522763269...
num_of_packets                                                15547
N

In [11]:
new_df

Label                                             Matrix
0          Youtube  [[9.5367431640625e-07, 15.143989086151123, 0.0...
1          Youtube  [[-1.2874603271484375e-05, 5.255686044692993, ...
2          Youtube  [[0.0, 8.029924869537354, 0.003217098073177249...
3          Youtube  [[0.0, 7.062128067016602, 0.002561701778292929...
4          Youtube  [[0.0, 5.052218198776245, 0.002312747371725172...
...            ...                                                ...
3927  Google Drive  [[-1.9073486328125e-06, 4.411745071411133, 0.0...
3928  Google Drive  [[1.9073486328125e-06, 11.05464482307434, 0.00...
3929  Google Drive  [[9.5367431640625e-07, 12.36051082611084, 0.00...
3930  Google Drive  [[2.86102294921875e-06, 3.7958312034606934, 0....
3931  Google Drive  [[1.3113021850585938e-05, 4.628432989120483, 0...

[3932 rows x 2 columns]

In [12]:
# Save DataFrame to a Parquet file using pyarrow
new_df.to_parquet('stnn_features.parquet', engine='pyarrow')

# Save DataFrame to CSV file
new_df.to_csv("stnn_features.csv", index=False)

### Problem solving

In [37]:
matrix = create_statistics_matrix(df.iloc[0,:])
print(matrix)

[1. 1. 0. ... 0. 1. 0.]
<class 'numpy.ndarray'>
0
<class 'int'>
22653
22652
[1. 1. 0. ... 0. 1. 0.]
<class 'numpy.ndarray'>
1
<class 'int'>
3247
3246
{'iat_min': 9.5367431640625e-07, 'iat_max': 5.992645025253296, 'iat_mean': 0.0027196397213849126, 'iat_std': 0.10185753631456705, 'iat_skew': 47.76948023385541, 'size_min': 89.0, 'size_max': 1412.0, 'size_mean': 1401.388160508542, 'size_std': 94.846296582863, 'size_skew': -10.196688837338659, 'total_packets': 22653, 'total_bytes': 31745646.0, 'packets_per_sec': 367.71199447807965, 'bytes_per_sec': 515307.23553856317}
[9.5367431640625e-07, 5.992645025253296, 0.0027196397213849126, 0.10185753631456705, 47.76948023385541, 89.0, 1412.0, 1401.388160508542, 94.846296582863, -10.196688837338659, 22653, 31745646.0, 367.71199447807965, 515307.23553856317]
[[-1.9073486328125e-06, 5.972417116165161, 0.0023794474668579033, 0.09481284554922456, 51.131058003398614, 89.0, 1412.0, 1242.074942084942, 430.56725058861224, -2.1757881672659827, 25900, 3216974

In [34]:
statistics_col = calculate_statistics_by_direction(df.iloc[0,:],1)
print(statistics_col)

[1. 1. 0. ... 0. 1. 0.]
<class 'numpy.ndarray'>
1
<class 'int'>
3247
3246
{'iat_min': 3.2901763916015625e-05, 'iat_max': 5.990344047546387, 'iat_mean': 0.018976704837801422, 'iat_std': 0.26815998283153986, 'iat_skew': 18.018628122161758, 'size_min': 97.0, 'size_max': 1412.0, 'size_mean': 130.61133353865105, 'size_std': 59.8635330903881, 'size_skew': 10.00483540120466, 'total_packets': 3247, 'total_bytes': 424095.0, 'packets_per_sec': 52.712421888966574, 'bytes_per_sec': 6884.839716969905}


In [20]:
def contains_nan(list_of_lists):
    # Flatten the list of lists and convert to a numpy array
    flattened_array = np.array([item for sublist in list_of_lists for item in sublist])
    
    # Check for NaNs
    return np.isnan(flattened_array).any()

In [21]:
def check_nan_in_dataset(df):
    # Apply the `contains_nan` function to each row's matrix
    df['Has_NaN'] = df['Matrix'].apply(contains_nan)
    return df

# Example usage
df_with_nan_check = check_nan_in_dataset(new_df)
print(df_with_nan_check)

           Label                                             Matrix  Has_NaN
0        Youtube  [[-1.9073486328125e-06, 5.972417116165161, 0.0...     True
1        Youtube  [[0.0, 9.354390859603882, 0.003731038111465003...     True
2        Youtube  [[-1.1920928955078125e-05, 7.244797945022583, ...     True
3        Youtube  [[-1.9073486328125e-06, 8.704989910125732, 0.0...     True
4        Youtube  [[0.0, 10.431927919387817, 0.00555849588458725...     True
5        Youtube  [[0.0, 15.403187990188599, 0.01212164598790228...     True
6        Youtube  [[-3.0994415283203125e-06, 5.99469780921936, 0...     True
7     Google Doc  [[-1.9073486328125e-06, 4.341797828674316, 0.0...     True
8     Google Doc  [[1.0967254638671875e-05, 3.5862808227539062, ...     True
9     Google Doc  [[2.002716064453125e-05, 5.092674016952515, 0....     True
10    Google Doc  [[1.9073486328125e-06, 9.54417109489441, 0.062...     True
11    Google Doc  [[9.5367431640625e-07, 3.384873151779175, 0.03...     True

In [ ]:
# Check for NaNs
df_with_nan_check = check_nan_in_dataset(new_df)
print(df_with_nan_check)

In [9]:
matrix = new_df.iloc[0,1]
print(type(matrix))

<class 'numpy.ndarray'>


In [34]:
# Sample array of arrays from a dataframe row
sample_data = [
    ['1522933033.872636000', '0', '1412', '1'],
    ['1522933033.872846000', '0.000209808', '350', '1'],
    ['1522933034.743008000', '0.870372', '930', '0']
]

# Convert the sample data to a 2D NumPy array
my_row = df.iloc[0]
my_array = df.iloc[0,1]

matrix = convert_to_2d_array(my_array)
matrix

array([[1.52293303e+09, 0.00000000e+00, 1.41200000e+03, 1.00000000e+00],
       [1.52293303e+09, 2.09808000e-04, 3.50000000e+02, 1.00000000e+00],
       [1.52293303e+09, 2.00310000e-02, 1.41200000e+03, 0.00000000e+00],
       ...,
       [1.52293310e+09, 6.15970000e+01, 1.27700000e+03, 0.00000000e+00],
       [1.52293310e+09, 6.15984000e+01, 1.23000000e+02, 1.00000000e+00],
       [1.52293310e+09, 6.16253000e+01, 1.49000000e+02, 0.00000000e+00]])

In [41]:
# Extract the timestamps
timestamps = matrix[:, 0].astype(float)
print(timestamps)

[1.52293303e+09 1.52293303e+09 1.52293303e+09 ... 1.52293310e+09
 1.52293310e+09 1.52293310e+09]


In [43]:
# Calculate inter-arrival times as differences between consecutive timestamps
inter_arrival_times = np.diff(timestamps)

print(inter_arrival_times)
print(np.min(inter_arrival_times))

[0.00020981 0.01982117 0.00114489 ... 0.00069284 0.00135708 0.02692604]
-1.9073486328125e-06


In [26]:
# Compute the statistics matrix for the current row
statistics_matrix = create_statistics_matrix(my_row)
statistics_matrix

<class 'numpy.ndarray'>
<class 'numpy.ndarray'>


In [25]:
# Extract the sizes
sizes = matrix[:, 2].astype(float)

print(sizes)

IndexError: too many indices for array: array is 1-dimensional, but 2 were indexed

In [68]:
packets = convert_to_2d_array(df.iloc[0,1])
print(packets[:,0])

diffs = precise_diff(packets[:,0])
print(min(diffs))
print(max(diffs))

[1.52293303e+09 1.52293303e+09 1.52293303e+09 ... 1.52293310e+09
 1.52293310e+09 1.52293310e+09]
[3033872636 3033872845 3033892667 ... 3095469662 3095471019 3095497946]
(array([22132], dtype=int64),)
5972418
[0.000209 0.019822 0.001144 ... 0.000692 0.001357 0.026927]
-1e-06
5.972418
